# 8. Data file formats

[Dataset download](https://s3.amazonaws.com/bebi103.caltech.edu/data/singer_transcript_counts.csv)

<hr>

In [1]:
# Colab setup ------------------
import os, sys, subprocess
if "google.colab" in sys.modules:
    cmd = "pip install --upgrade iqplot fcsparser pynwb watermark"
    process = subprocess.Popen(cmd.split(), stdout=subprocess.PIPE, stderr=subprocess.PIPE)
    stdout, stderr = process.communicate()
    data_path = "https://s3.amazonaws.com/bebi103.caltech.edu/data/"
else:
    data_path = "../data/"

In [2]:
import pandas as pd
import numpy as np

import h5py
import fcsparser
import pynwb

import iqplot

import bebi103

import bokeh.io
bokeh.io.output_notebook()

Loading BokehJS ...

<hr>

Data sets, biological and otherwise, come in a large variety of formats, being acquired using an even larger variety of instruments. The ability to read and parse data sets in different formats is a key part of data wrangling.

There is no real prescribed procedure to handle various data file formats, so I instead give a few tips here.

1. If the file format is proprietary, obtain documentation from the instrument manufacturer or whoever produced the file format. If the documentation is not available, call the company to obtain assistance. If no information is available, avoid using the format; _don't guess._
2. If you are using a proprietary format, try to find a way to convert the data set to an open format. Depending on what field you are working in, there may be automated converters available. For example, you can convert a lot of proprietary microscopy formats to the open [OME-TIFF](https://docs.openmicroscopy.org/ome-model/latest/ome-tiff/) format using [Bio-Formats](https://www.openmicroscopy.org/bio-formats/).
3. For open file formats, carefully read the documentation of the file format. This may require some Googling.
4. If you need to read in file formats into Pandas data frames, Numpy array, or other familiar Python classes, there are often packages available to do so, and these are usually described in the documentation of the file format.
5. When reading in data, make sure you get it all. **Metadata** are data that provide information about other data, presumably the "main" content of a data set. (I often do not make this distinction; metadata are data!) Be sure you know how to access the metadata within a given file format.

These tips are not immediately helpful for any given file format. To demonstrate how to handle various file formats, I will give a few examples. Ultimately, though, it is your responsibility as an analyst of data to learn and understand the file format to make sure you completely and accurately can conveniently access a data set. I argue further that as a data *producer*, you are responsible for storing *and sharing* your data in an open, easily accessible, well-documented file format.

With that, I proceed to the examples.

## Reading data from MS Excel

You will often find collaborators, and sometimes instruments, provide data in as [Microscoft Excel](https://en.wikipedia.org/wiki/Microsoft_Excel) documents. Prior to 2007, the Excel format was proprietary, but now it is open. This has allowed Python developers to write parsers of Excel files.

As an example of reading from an Excel file, we will open a data set from [David Lack](https://en.wikipedia.org/wiki/David_Lack). The data set, available [from Dryad](https://doi.org/10.5061/dryad.150), and downloadable [here](https://s3.amazonaws.com/bebi103.caltech.edu/data/morphLack.xls), contain Lack's morphological measurements of finches taken from the Galápagos in 1905 and 1906 and stored in the California Academy of Sciences. These measurements were the basis for his famous book _Darwin's Finches_.

Reading in the data is as simple as using `pd.read_excel()`. For Excel documents with multiple sheets or more complicated layouts, be sure to [read the docs](https://pandas.pydata.org/docs/reference/api/pandas.read_excel.html). As with `pd.read_csv()`, there are lots of useful kwargs.

In [3]:
# Read the data in
df = pd.read_excel(os.path.join(data_path, "morphLack.xls"))

# Take a look
df.head()

Source IslandID              TaxonOrig  GenusL69    SpeciesL69 SubspL69  \
0  Lack CAS  Wlf_Wnm  Geospiza magnirostris  Geospiza  magnirostris      NaN   
1  Lack CAS  Wlf_Wnm  Geospiza magnirostris  Geospiza  magnirostris      NaN   
2  Lack CAS  Wlf_Wnm  Geospiza magnirostris  Geospiza  magnirostris      NaN   
3  Lack CAS  Wlf_Wnm  Geospiza magnirostris  Geospiza  magnirostris      NaN   
4  Lack CAS  Wlf_Wnm  Geospiza magnirostris  Geospiza  magnirostris      NaN   

  SpeciesID  SubspID Sex Plumage  BodyL  WingL  TailL  BeakW  BeakH  LBeakL  \
0   Geo.mag  Geo.mag   M   Black    NaN   86.0    NaN    NaN   20.7     NaN   
1   Geo.mag  Geo.mag   M   Black    NaN   86.0    NaN    NaN   19.5     NaN   
2   Geo.mag  Geo.mag   M   Black    NaN   88.0    NaN    NaN    NaN     NaN   
3   Geo.mag  Geo.mag   M   Black    NaN   84.0    NaN    NaN   20.6     NaN   
4   Geo.mag  Geo.mag   M   Black    NaN   86.0    NaN    NaN   21.4     NaN   

   UBeakL  N-UBkL  TarsusL  MToeL  
0    22.8    15.7      NaN    NaN  
1    24.3    16.6      NaN    NaN  
2    23.1    15.1      NaN    NaN  
3    22.4    15.3      NaN    NaN  
4    23.1    15.4      NaN    NaN

Aside from Pandas, there are several other Excel readers available, as described at [http://www.python-excel.org](http://www.python-excel.org). For more fine-grained control of reading in the data from Excel spreadsheets, you might want to use `xlrd` for older documents (which the Lack data actually is, but Pandas handles it), and `openpyxl` for newer documents.

## Example: Flow cytometry data

[Flow cytometry](https://en.wikipedia.org/wiki/Flow_cytometry) is a technique in which cells are run single file through a fluid channel and subjected to illumination by a laser. The front and side scatters of the light are measured, as is the fluorscence intensity emitted if a cells contain fluorophores. 

The technique is many decades old. Most often, flow cytometry data are stored in [flow cyometry standard (FCS) format](https://en.wikipedia.org/wiki/Flow_Cytometry_Standard). These are binary files that cannot be directly read in using Pandas. As such, there are a few options we can pursue for reading FCS files and getting them into a format to work with.

1. Use commercial software like [FlowJo](https://en.wikipedia.org/wiki/FlowJo) to open the file, and use it for analysis or for save in the data as CSV.
2. Study the [FCS specification](https://dx.doi.org/10.1002%2Fcyto.a.20825) and write our own parser to open FCS files and store the content in a data frame.
3. Look for packages that provide parsers.

In almost all cases for file formats, option (3) is preferred. A cursory Google search reveals several Python-based packages for opening FCS files and storing them in convenient formats (and also performing analysis).

- [CytoFlow](https://cytoflow.github.io)
- [CytoPy](https://cytopy.readthedocs.io/)
- [FlowCytometryTools](https://eyurtsev.github.io/FlowCytometryTools/)
- [fcm](https://pythonhosted.org/fcm/basic.html)
- [fcsparser](https://github.com/eyurtsev/fcsparser)

There is quite a variety in these packages, particularly in terms of their scope. Several aim to facilitate standard analyses of flow cytometry data. fcsparser, conversely, simply aims to read in an FCS file so that you can use its contents in a Pandas data frame. This is the functionality we desire here.

### Use conda environments!

In order to use `fcsparser`, we need to install it. It is not included in the `bebi103` environment because it has earlier versions of Pandas as a dependency. This is fairly common in domain-specific packages; they often have restrictive dependencies. **I advise creating a new conda environment for domain specific tasks.** That is what I have done in this notebook.

As an example, we will use [this FCS](https://s3.amazonaws.com/bebi103.caltech.edu/data/20160804_wt_O2_HG104_0uMIPTG.fcs), which was part of [this paper](https://doi.org/10.1016/j.cels.2018.02.004) by Razo-Mejia, et al. (The complete set of FCS files used in that paper are available [here](https://doi.org/10.22002/D1.224).)
Given its simple scope, providing a tool to read CSV files into data frames, usage of fcsparser is simple and may be ascertained from its equally simple [documentation](https://github.com/eyurtsev/fcsparser#using).

In [4]:
metadata, df = fcsparser.parse(
    os.path.join(data_path, "20160804_wt_O2_HG104_0uMIPTG.fcs")
)

# Take a look
df.head()

HDR-T         FSC-A        FSC-H          FSC-W         SSC-A  \
0  0.418674   6537.148438  6417.625000  133513.125000  24118.714844   
1  2.563462   6402.215820  5969.625000  140570.171875  23689.554688   
2  4.921260   5871.125000  5518.852539  139438.421875  16957.433594   
3  5.450112   6928.865723  8729.474609  104036.078125  13665.240234   
4  9.570750  11081.580078  6218.314453  233581.765625  43528.683594   

          SSC-H          SSC-W        FITC-A       FITC-H         FITC-W  \
0  22670.142578  139447.218750  11319.865234  6816.254883  217673.406250   
1  22014.142578  141047.390625   1464.151367  5320.254883   36071.437500   
2  17344.511719  128146.859375   5013.330078  7328.779785   89661.203125   
3  11657.869141  153641.312500    879.165771  6997.653320   16467.523438   
4  22722.318359  251091.968750   2271.960693  9731.527344   30600.585938   

    APC-Cy7-A   APC-Cy7-H     APC-Cy7-W  
0   55.798954  255.540833  28620.398438  
1   74.539612  247.540833  39468.460938  
2  -31.788519  229.903214 -18123.212891  
3  118.226028  362.191162  42784.375000  
4   20.693352  210.486893  12885.928711

Very nice! Now we can unleash all of our Python-based analysis tools on flow cytometry data sets, and we will soon when we use this data set in some overplotting examples.

We can also save the data as a CSV file for future use using the `to_csv()` method,

    df.to_csv('20160804_wt_O2_HG104_0uMIPTG.csv', index=False)
    
thereby eliminating the need for a special parser down the road.

Note, though, that **you should never delete the raw data file that came from the data source**, even if its format is inconvenient.

## Example: Electrophysiologial recordings of neurons in the human brain

As an example of a file format specific to a given field, we will open up an NWB ([Neurodata Without Borders](https://www.nwb.org)) file. NWB was created as a standard for neuroscience data so that they may be shared across research groups. This is stated clearly in [their description of the data standard](https://www.nwb.org/nwb-neurophysiology/): 

Neurodata Without Borders (NWB) is a data standard for neurophysiology, providing neuroscientists with a common standard to share, archive, use, and build common analysis tools for neurophysiology data. NWB is designed to store a variety of neurophysiology data, including data from intracellular and extracellular electrophysiology experiments, data from optical physiology experiments, and tracking and stimulus data. The project includes not only the NWB format, but also a broad range of software for data standardization and application programming interfaces (APIs) for reading and writing the data as well as high-value data sets that have been translated into the NWB data standard.)

NWB files are stored in [HDF5 format](https://en.wikipedia.org/wiki/Hierarchical_Data_Format) with a [specific schema for their structure](https://doi.org/10.1101/523035) (with a more detailed schema [here](https://nwb-schema.readthedocs.io/)). Therefore, we can use an HDF5 parser to explore NWB data sets.

HDF stands for "hierarchical data format," meaning that a single HDF file can contain a file system-like structure of data. Each entry is either a **dataset**, which contains an array of data, or a **group**, which contains data sets an other groups. You can think of groups like directories in a file system. Both datasets and groups can have arbitrary **attributes** which are (possibly formless) metadata. Importantly, HDF5 files are highly optimized for large data sets. When working with them, you do not need to store the data in RAM, but can rapidly access portions of the data from disk as needed.

To see how this works, let's consider an example. We will work with the file `sub-P14HMH_ses-20070601_obj-7studd_ecephys+image.nwb`, available [here](https://s3.amazonaws.com/bebi103.caltech.edu/data/sub-P14HMH_ses-20070601_obj-7studd_ecephys+image.nwb). It may also be directly downloaded from the [DANDI Archive](https://dandiarchive.org/) by clicking [here](https://api.dandiarchive.org/api/assets/8144c86f-c7fa-4599-9a31-6db621deb6a5/download/). The data set comes from the lab or [Ueli Rutishauser](https://www.cedars-sinai.edu/research/labs/rutishauser.html) at Cedars-Sinai. It was featured in a [publication describing NWB by Chandravadia, et al.](https://doi.org/10.1038/s41597-020-0415-9), originally coming from their paper by [Faraut, et al.](https://doi.org/10.1038/sdata.2018.10) highlighting the data set on declarative memory encoding and recognition in humans. The data set includes recordings from single neurons from human amygdala and hippocampus. The subjects were shown a set of images. They were then shown another set of images, some of which they had already seen. Neuronal spike times were recorded during this process. We will look at a portion of this data set measured from electrodes in the right amygdala and left hippocampus of a single subject, a 31-year-old male. The entire data set is freely available from the [DANDI archive](https://gui.dandiarchive.org/#/dandiset/000004/).

As we work through this example, note that there are **many** file formats across fields, and this serves as an example of one and how you might navigate the format to pull out what you need for your analysis. I note that prior to writing this section of the lesson, I have never opened an NWB file nor used h5py much at all. I used a skill you will hopefully master: asking the internet for help. I show this and the other examples to illustrate to you that you will encounter file formats you may not be familiar with, and you need to be patient and search and read carefully how to use appropriate tools to parse them.

### Parsing the file with h5py

The [h5py package](https://docs.h5py.org/) enables opening and navigating HDF5 files. It takes advantage of HDF5's structure to enable access of the data on disk without copying the whole thing into RAM. We have imported h5py above and can use it to open the file.

In [5]:
with h5py.File(
    os.path.join(data_path, "sub-P14HMH_ses-20070601_obj-7studd_ecephys+image.nwb"), "r"
) as f:
    print(f)

<HDF5 file "sub-P14HMH_ses-20070601_obj-7studd_ecephys+image.nwb" (mode r)>


Note that we have used `h5py.File()` to instantiate a `File` instance to get access to the data in the file. I am using context management here to keep me out of trouble for reading and writing files, just as we did when we learned about file I/O in an earlier lesson.

After opening the file, I printed it, which is an HDF5 `File` instance. These behave much like dictionaries, and I can see the keys of the dictionary using the `keys()` method.

In [6]:
with h5py.File(
    os.path.join(data_path, "sub-P14HMH_ses-20070601_obj-7studd_ecephys+image.nwb"), "r"
) as f:
    print(f.keys())

<KeysViewHDF5 ['acquisition', 'analysis', 'file_create_date', 'general', 'identifier', 'intervals', 'processing', 'session_description', 'session_start_time', 'stimulus', 'timestamps_reference_time', 'units']>


We see that the HDF file contains groups acquisition, analysis, etc. It would be useful to crawl the whole hierarchical structure of the file, something like `ls -R` on the command line. This is possible using the `visititems()` method. It takes a single argument, which is a function you want applied to each item in the hierarchy of the file. To view what we have, the `print()` function will work fine.

In [7]:
with h5py.File(
    os.path.join(data_path, "sub-P14HMH_ses-20070601_obj-7studd_ecephys+image.nwb"), "r"
) as f:
    f.visititems(print)

acquisition <HDF5 group "/acquisition" (2 members)>
acquisition/events <HDF5 group "/acquisition/events" (2 members)>
acquisition/events/data <HDF5 dataset "data": shape (754,), type "|O">
acquisition/events/timestamps <HDF5 dataset "timestamps": shape (754,), type "<f8">
acquisition/experiment_ids <HDF5 group "/acquisition/experiment_ids" (2 members)>
acquisition/experiment_ids/data <HDF5 dataset "data": shape (754,), type "<f8">
acquisition/experiment_ids/timestamps <HDF5 dataset "timestamps": shape (754,), type "<f8">
analysis <HDF5 group "/analysis" (0 members)>
file_create_date <HDF5 dataset "file_create_date": shape (1,), type "|O">
general <HDF5 group "/general" (9 members)>
general/data_collection <HDF5 dataset "data_collection": shape (), type "|O">
general/devices <HDF5 group "/general/devices" (1 members)>
general/devices/Neuralynx-cheetah <HDF5 group "/general/devices/Neuralynx-cheetah" (0 members)>
general/experiment_description <HDF5 dataset "experiment_description": shap

To access a group or dataset from the `File` instance, we index like a dictionary with the "path" to the object of interest. So, for example, say we wanted to find the time point when stimuli were presented to the subject, we can index as follows. (Going foward, we will not use context management just to avoid code clutter, and will close the `File` instance when we are done. Generally, though, you should use context management, as when doing file I/O.)

In [8]:
f = h5py.File(
    os.path.join(data_path, "sub-P14HMH_ses-20070601_obj-7studd_ecephys+image.nwb"), "r"
)

f["intervals/trials/stim_on_time"]

<HDF5 dataset "stim_on_time": shape (150,), type "<f8">

Note that we see this as a dataset consisting 150 64-bit floating point numbers (`f8`). The data set has not yet been accessed, but it is available for use, almost exactly like a NumPy array. Importantly, they support much of Numpy's fancy indexing and slicing. If we do want direct access of the entire array as a Numpy array, we index with an empty tuple `[()]` or `[tuple()]`.

In [9]:
f['intervals/trials/stim_on_time'][()]

array([3018.31409 , 3023.236694, 3027.561148, 3031.890272, 3036.014586,
       3039.860668, 3043.831013, 3048.447768, 3053.086304, 3058.577719,
       3062.238007, 3067.642116, 3072.621551, 3077.625471, 3082.789226,
       3088.027263, 3092.089399, 3096.196786, 3100.801929, 3105.771749,
       3110.665814, 3114.849509, 3118.918742, 3123.272534, 3128.122392,
       3132.590985, 3137.111894, 3141.603956, 3147.717728, 3153.470202,
       3158.333761, 3168.646004, 3175.345146, 3179.651875, 3184.451598,
       3188.370026, 3192.887064, 3197.331327, 3201.374939, 3205.493293,
       3209.305061, 3213.320073, 3217.695492, 3222.133979, 3226.03333 ,
       3230.202833, 3234.002927, 3237.959018, 3241.884543, 3245.480595,
       3956.716701, 3963.177978, 3969.633632, 3974.25094 , 3978.264324,
       3984.13252 , 3989.92923 , 3995.180906, 4002.849509, 4008.402487,
       4012.75376 , 4017.317062, 4022.795421, 4031.293864, 4037.318977,
       4043.365779, 4047.332315, 4054.664626, 4061.639448, 4067.

We can use Bokeh's image visualization to see what the stimulus images were. For example, let look at image number 125. (For convenience, we will use the `imshow()` function of the [bebi103 package](https://bebi103.github.io).)

In [10]:
# Pull out first stimulus
stim_im = f['stimulus/presentation/StimulusPresentation/data'][125][()]

# View the image
bokeh.io.show(bebi103.image.imshow(stim_im))

Now, to do something interesting with the data, we can look at the number of spikes recorded from all electrodes while viewing a stimulus during training (before the subject has to answer whether or not he has seen the stimulus before), when the image is novel (not seen before) or familiar (seen before).

First, we pull out the information about the type of image.

In [11]:
stim_type = f['intervals/trials/new_old_labels_recog'][()]

# Take a look
stim_type

array([b'NA', b'NA', b'NA', b'NA', b'NA', b'NA', b'NA', b'NA', b'NA',
       b'NA', b'NA', b'NA', b'NA', b'NA', b'NA', b'NA', b'NA', b'NA',
       b'NA', b'NA', b'NA', b'NA', b'NA', b'NA', b'NA', b'NA', b'NA',
       b'NA', b'NA', b'NA', b'NA', b'NA', b'NA', b'NA', b'NA', b'NA',
       b'NA', b'NA', b'NA', b'NA', b'NA', b'NA', b'NA', b'NA', b'NA',
       b'NA', b'NA', b'NA', b'NA', b'NA', b'0', b'1', b'0', b'1', b'1',
       b'1', b'0', b'1', b'1', b'1', b'1', b'0', b'0', b'1', b'0', b'0',
       b'1', b'0', b'1', b'1', b'1', b'0', b'1', b'0', b'0', b'1', b'0',
       b'1', b'1', b'0', b'0', b'1', b'0', b'0', b'0', b'1', b'0', b'1',
       b'1', b'1', b'1', b'0', b'0', b'1', b'0', b'0', b'1', b'1', b'0',
       b'0', b'1', b'0', b'1', b'0', b'1', b'1', b'0', b'1', b'0', b'0',
       b'1', b'1', b'1', b'0', b'0', b'1', b'0', b'1', b'1', b'1', b'0',
       b'0', b'0', b'1', b'1', b'0', b'0', b'0', b'0', b'1', b'1', b'0',
       b'0', b'0', b'0', b'0', b'1', b'1', b'0', b'1', b'1', b'1', 

Here, `NA` means it was a training image, `0` means that the subject had not seen the image before, and `1` means that they had. Note also that these are all byte strings, which we should convert to strings to play nicely with Bokeh. We might as well make them more descriptive in the meantime.

In [12]:
rename = {b'NA': "training", b"1": "familiar", b"0": "novel"}
stim_type = np.array([rename[st] for st in stim_type])

t_on = f['intervals/trials/stim_on_time']
t_off = f['intervals/trials/stim_off_time']

Finally, we pull out the records of the spikes.

In [13]:
spike_times = f['units/spike_times'][()]

Now, we can compute the spike rate (the number of observed spikes divided by the time the simulus was present) for each stimulus.

In [14]:
spike_rate = np.empty_like(t_on)
for i, (t1, t2) in enumerate(zip(t_on, t_off)):
    spike_rate[i] = np.sum((spike_times > t1) & (spike_times < t2)) / (t2 - t1)

We can toss these data into a data frame for convenient plotting. It will help to change the values of the stimulus types to be more descriptive.

In [15]:
df = pd.DataFrame(
    data={
        "stimulus type": stim_type,
        "spike rate (Hz)": spike_rate,
        "stimulus index": np.arange(len(stim_type)),
    }
)

Now we can make a plot!

In [16]:
p = iqplot.ecdf(
    df,
    q='spike rate (Hz)',
    cats='stimulus type',
    tooltips=[('stim ind', '@{stimulus index}')]
) 

bokeh.io.show(p)

In looking at the ECDF, there seems to be a higher spiking rate during training than not, and no real difference between presentation of novel versus familiar stimuli. By hovering over the point with the highest spike rate, we see that it is image 78. Let's take a look!

In [17]:
# Pull out stimulus 78
stim_im = f['stimulus/presentation/StimulusPresentation/data'][78][()]

# View the image
bokeh.io.show(bebi103.image.imshow(stim_im))

Oooo! A scary shark! It has scared us into remembering to close the file.

In [18]:
f.close()

### A domain-specific tool

While directly using h5py works just fine, as we have seen, the neuroscience community has built their own package for handling NWB files, [pwnwb](https://pynwb.readthedocs.io/). You can install it using

    pip install pynwb
  
But you should do it in a separate environment (it is *not* in the `bebi103` environment). Instead of using dictionary-like indexing, pynwb enables access to data using functions specific to neuroscience data sets. For example, we can conveniently pull out the spike times of all spikes measured from a single neuron, say neuron with index 10. I deduced the syntax for doing this by reading the [pynwb docs](https://pynwb.readthedocs.io/).

In [19]:
# Open the file
raw_io = pynwb.NWBHDF5IO(
    os.path.join(data_path, "sub-P14HMH_ses-20070601_obj-7studd_ecephys+image.nwb"), "r"
)

# Read the content
nwb_in = raw_io.read()

# Pull out spike times of neuron with index 10
spike_times = nwb_in.units.get_unit_spike_times(10)

For many data types, domain specific tools exist and can be quite useful. I tend to only use them for parsing, slicing, accessing, and organizing data, but prefer to use my own bespoke methods for analysis.

## Computing environment

In [20]:
%load_ext watermark
%watermark -v -p numpy,pandas,h5py,pynwb,bokeh,bebi103,iqplot,jupyterlab

Python implementation: CPython
Python version       : 3.11.5
IPython version      : 8.15.0

numpy     : 1.24.3
pandas    : 1.5.3
h5py      : 3.9.0
pynwb     : 2.5.0
bokeh     : 3.2.1
bebi103   : 0.1.17
iqplot    : 0.3.5
jupyterlab: 4.0.6

